In [2]:
import pandas as pd
import numpy as np
import re
import json
import nltk
from word2number import w2n
from nltk.stem.snowball import SnowballStemmer
import random

In [9]:
# file = "math23k_0108.json"
# df = pd.read_json(file)

# For dolphine use:
df = pd.read_csv('trainData_univariable.csv')
df = df[np.invert(np.array(df['cleaned_text'].isna()))] #not sure what this is doing .. check
df.head()

text  ans  \
0  What is the sum of the distinct prime factors ...  226   
1  Fifteen more than four times a number is 6 mor...    9   
2  5 less than 6 times a whole number is 9 less t...    2   
3  1/3 of a number is 5 less than half of the sam...   30   
4  I think of a number multiply it by 8 then subt...   11   

               equations unknowns  \
0            s = 3 + 223        s   
1     15 + 4*n = 6 + 5*n        n   
2      6*n - 5 = 8*n - 9        n   
3  1/3 * x = 1/2 * x - 5        x   
4         8*x - 66 = 2*x        x   

                                        cleaned_text  
0                    sum distinct prime factors 2007  
1  fifteen more than four times a number 6 more t...  
2  5 less than 6 times a whole number 9 less than...  
3        1/3 a number 5 less than half number number  
4  think a number multiply 8 subtract 66 result t...

In [63]:
# with open("Math23K.json") as f:
#     data = json.loads(f)
data = pd.read_json("Math23K.json")
data = data.rename(columns={"id":"iIndex","segmented_text":"sQuestion","equation":"iEquation","ans":"solution"})
data.reset_index(drop=True, inplace=True)
# data = data[:2000]
data.head()

iIndex                                      original_text  \
0       1  镇海雅乐学校二年级的小朋友到一条小路的一边植树．小朋友们每隔2米种一棵树（马路两头都种了树）...   
1       2  1个工程队挖土，第一天挖了316方，从第2天开始每天都挖230方，连续挖了6天，这个工程队一...   
2       3  小明看一本故事书，第一天看了全书的(1)/(6)，第2天看了24页，第3天看的页数是前两天看...   
3       4  从甲地到乙地，如果骑自行车每小时行驶16千米，4小时可以到达，如果乘汽车只需要2小时，汽车每...   
4       5             小刚的体重是28.4千克，小强的体重是小刚的1.4倍，小强的体重=多少千克？   

                                           sQuestion  \
0  镇海 雅乐 学校 二年级 的 小朋友 到 一条 小路 的 一边 植树 ． 小朋友 们 每隔 ...   
1  1 个 工程队 挖土 ， 第一天 挖 了 316 方 ， 从 第 2 天 开始 每天 都 挖...   
2  小 明 看 一本 故事书 ， 第一天 看 了 全书 的 (1)/(6) ， 第 2 天 看 ...   
3  从 甲地 到 乙地 ， 如果 骑 自行车 每 小时 行驶 16 千米 ， 4 小时 可以 到...   
4  小 刚 的 体重 是 28.4 千克 ， 小强 的 体重 是 小 刚 的 1.4 倍 ， 小...   

                                       iEquation solution  
0                                     x=(11-1)*2       20  
1                                x=316+230*(6-1)     1466  
2  x=(24+24*150)/(1-(1)/(6)-(1)/(6)*150-(1)/(4))      180  
3                                       x=16*4/2       32  
4                                     x=28.4*1.4    39.76

In [64]:
data[data.index==2254]
data.shape

(23162, 5)

In [65]:
datajson = data.to_json(orient='index')
with open('math_json_wy.json', 'w') as f:
    json.dump(datajson, f)

In [66]:
with open('math_json_wy.json') as f:
    data = json.load(f)
data = json.loads(data)

In [70]:
def split_num_and_unit(word):
    num = ''
    unit = ''
    for idx in range(len(word)):
        char = word[idx]
        if char.isdigit() or char in ['.', '/', '(', ')']:
            num += char
        else:
            unit += word[idx:]
            break
    return num, unit#.encode('utf-8')

def mask_num(seg_text_list, equ_str):
    alphas = 'abcdefghijklmnopqrstuvwxyz'
    num_list  = []
    mask_seg_text = []
    numtemp_order = []
    num_pos = []
    pos=-1
    count = 0 
    for word in seg_text_list:
        pos+=1
        if word == '':
            continue
        if is_number(word):
            mask_seg_text.append("temp_"+alphas[count])
            numtemp_order.append("temp_"+alphas[count])
            if '%' in word:
                mask_seg_text.append('%')
            num_list.append(word)
            num_pos.append(pos)
            count += 1
        else:
            mask_seg_text.append(word)
    mask_equ_list = []
    s_n = sorted([(w,i) for i,w in enumerate(num_list)], key=lambda x: len(str(x[0])), reverse=True)
#     print("tonda", s_n)
    if '3.14%' not in equ_str and '3.1416' not in equ_str:
        equ_str = equ_str.replace('3.14', '&PI&', 15)
    for num, idx in s_n:
#         num = num_list[idx]
#         print(num)
        if num[-1] == '%':
            num = num[:-1]
        
        equ_str = equ_str.replace(num, '&temp_'+alphas[idx]+'&', 15)
    equ_list = []
#     print(equ_str)
    num_set = ['0','1','2','3','4','5','6','7','8','9','%', '.']
    for elem in equ_str.split('&'):
        if 'temp' in elem or 'PI' in elem:
            equ_list.append(elem)
        else:
            start = ''
            for char in elem:
                if char not in num_set:
                    if start != '':
                        equ_list.append(start)
#                         print("start ",start)
#                     print("character  is ",char)
                    equ_list.append(char)
                    start = ''
                else:
                    start += char
            if start != '':
                equ_list.append(start)
    reverse_equ_list = equ_list[::-1]
    #reverse_equ_list.append('END_token')
    #equ_list.append('END_token')
#     print(mask_seg_text,num_list,numtemp_order,num_pos)
    return mask_seg_text, num_list, equ_list, reverse_equ_list, numtemp_order, num_pos
def is_number(word):
    if word[0] == '(' and word[-1] == ')':
        return True
    #if word[0] == '(' and word[1].isdigit() and not word[-1].isdigit():
    #    return True
    if '(' in word and ')' in word and '/' in word and not word[-1].isdigit():
         return True
    if word[-1] == '%' and len(word)>1:
        return True
    if word[0].isdigit():
        return True
    try:
        float(word)
        return True
    except:
        return False
def extract_number_and_align_per(data_per):
    wp_id = data_per['iIndex']
    seg_text = data_per['sQuestion']
    equation = data_per['iEquation']
    equation = re.sub('\[', '(', equation)
    equation = re.sub('\]', ')', equation)
    ans = data_per['solution']

    num_list = []
    word_seg_list = []
    for word in seg_text.split(' '):
        if word == '' or word == ' ':
            continue 
        if is_number(word):
#             print(word)
            if '(' not in word and '%' not in word and ( not word[-1].isdigit() or (len(word) > 2 and not word[-2].isdigit())) :
                num, unit = split_num_and_unit(word)
                word_seg_list.append(num)
                word_seg_list.append(unit)
            elif '(' in word and word[-1] != ')' and ( not word[-1].isdigit() or (len(word) > 2 and not word[-2].isdigit())):
                num, unit = split_num_and_unit(word)
                word_seg_list.append(num)
                word_seg_list.append(unit)
            else:
                word_seg_list.append(word) 
        else:
            word_seg_list.append(word)
                 
    print(word_seg_list)
    mask_seg_text_list, num_list, mask_equ_list, mask_inv_equ_list,numtemp_order,num_pos = mask_num(word_seg_list, equation)
    return [mask_seg_text_list, mask_equ_list, num_list, mask_inv_equ_list,numtemp_order, num_pos]

In [71]:
data_dict = {}
data_all=data
i=0
for key in data_all:
    elem = data_all[key]
    key = elem['iIndex']
    if str(key) in ['8882', '10430']:
        continue
#     print(elem)
    tuple_per = extract_number_and_align_per(elem)
    data_dict[key] = {}
    data_dict[key]['tuple'] = tuple_per
    data_dict[key]['sQuestion'] = elem['sQuestion'][:]
    data_dict[key]['iEquation'] = elem['iEquation'][:]
    data_dict[key]['solution'] = elem['solution'][:]
    data_dict[key]['iIndex'] = elem['iIndex']
#     print(tuple_per)
#     print(data_dict[key]['iEquation'])
    i+=1
#     if(i==200):
#         break
    

['镇海', '雅乐', '学校', '二年级', '的', '小朋友', '到', '一条', '小路', '的', '一边', '植树', '．', '小朋友', '们', '每隔', '2', '米', '种', '一棵树', '（', '马路', '两头', '都', '种', '了', '树', '）', '，', '最后', '发现', '一共', '种', '了', '11', '棵', '，', '这', '条', '小路', '长', '多少', '米', '．']
['1', '个', '工程队', '挖土', '，', '第一天', '挖', '了', '316', '方', '，', '从', '第', '2', '天', '开始', '每天', '都', '挖', '230', '方', '，', '连续', '挖', '了', '6', '天', '，', '这个', '工程队', '一周', '共', '挖土', '多少', '方', '？']
['小', '明', '看', '一本', '故事书', '，', '第一天', '看', '了', '全书', '的', '(1)/(6)', '，', '第', '2', '天', '看', '了', '24', '页', '，', '第', '3', '天', '看', '的', '页数', '是', '前两天', '看', '的', '总数', '的', '150%', '，', '这时', '还有', '全书', '的', '(1)/(4)', '没有', '看', '，', '那么', '这', '本书', '一共', '多少', '页', '．']
['从', '甲地', '到', '乙地', '，', '如果', '骑', '自行车', '每', '小时', '行驶', '16', '千米', '，', '4', '小时', '可以', '到达', '，', '如果', '乘', '汽车', '只', '需要', '2', '小时', '，', '汽车', '每', '小时', '行驶', '多少', '千米', '？']
['小', '刚', '的', '体重', '是', '28.4', '', '千克', '，', '小强', '的', '体重', '是', '小', '刚

['华侨', '小学', '举行', '广播操', '比赛', '，', '三年级', '共有', '189', '人', '，', '准备', '9', '人', '站', '一行', '，', '一共', '要', '站', '多少', '行', '？']
['甲', '仓库', '有', '化肥', '120', '吨', '，', '乙', '仓库', '比', '甲', '仓库', '多', '20%', '，', '两个', '仓库', '共有', '化肥', '多少', '吨', '？']
['小', '明', '数学', '考', '了', '85', '分', '，', '比', '语文', '少', '考', '(2)/(19)', '，', '比', '语文', '少', '考', '多少', '分', '？']
['菜场', '用', '相同', '的', '卡车', '运', '蔬菜', '．', '先', '用', '4', '辆车', '共', '运走', '了', '640', '箱', '，', '再', '用', '3', '辆车', '就', '可', '全部', '运', '完', '．', '菜场', '一共', '运', '了', '多少', '箱', '蔬菜', '？']
['1', '块', '麦地', '，', '去年', '共', '收', '小麦', '1327', '千克', '，', '今年', '一共', '收', '了', '35', '袋', '，', '每', '袋', '53', '千克', '，', '今年', '比', '去年', '多', '收', '多少', '千克', '？']
['学校', '体操队', '有', '36', '人', '，', '合唱队', '比', '体操队', '人数', '的', '2', '倍', '少', '4', '人', '，', '合唱队', '多少', '人', '？']
['1', '台', '电视机', '降价', '20%', '后', '售价', '1200', '元', '，', '降价', '了', '多少', '元', '？']
['“', '国庆', '”', '期间', '，', '中央', '国际', '新亚', '商城', '搞'

['自行车厂', '去年', '生产', '自行车', '6000', '辆', '，', '今年', '生', '生产', '自行车', '7200', '辆', '，', '今年', '比', '去年', '增产', '百分之几', '？']
['1', '杯', '果汁', '，', '喝', '了', '(4)/(6)', '，', '杯中', '还有', '几分', '之', '几', '？']
['修', '一条', '路', '，', '已修', '和', '未', '修', '的', '千米', '数', '比', '是', '3', '：', '5', '．', '如果', '再', '修', '12', '千米', '，', '则', '已修', '的', '和', '未', '修', '的', '千米', '数', '比', '为', '9', '：', '11', '．', '这', '条', '路', '共', '长', '多少', '千米', '？']
['某', '化肥厂', '全年', '计划', '生产', '化肥', '40', '万吨', '，', '上半年', '生产', '了', '23', '万吨', '，', '上半年', '完成', '了', '全年', '计划', '的', '百分之几', '？']
['甲', '、', '乙', '两辆', '汽车', '，', '甲', '在', '西', '地', '，', '乙', '在', '东', '地', '，', '同时', '向东', '开行', '．', '甲', '每', '小时', '行', '60', '千米', '，', '乙', '每', '小时', '行', '48', '千米', '，', '行', '了', '5', '小时', '后', '，', '甲', '在', '乙', '后面', '24', '千米', '处', '．', '那么', '东西', '两地', '相隔', '多少', '千米', '．']
['1', '辆', '汽车', '0.3', '', '小时', '行使', '15', '千米', '，', '用', '同样', '的', '速度', '，', '从', '甲', '站', '开往', '乙', '站', '需要'

['多少', '的', '12', '倍', '是', '420', '．']
['某', '军', '排', '着', '300', '米', '长', '的', '队伍', '行军', '，', '速度', '是', '4', '米', '/', '秒', '，', '走', '在', '队伍', '最后', '的', '通讯员', '，', '接到', '命令', '后', '立即', '以', '8', '米', '/', '秒', '的', '速度', '追赶', '走', '在', '最', '前面', '的', '指挥员', '，', '追', '到', '后', '又', '立即', '以', '相同', '速度', '返回', '原来', '位置', '，', '从', '接到', '命令', '到', '返回', '原位', '共用', '多少', '秒', '？']
['甲', '数', '的', '(1)/(5)', '是', '10', '，', '则', '它', '的', '25%', '=', '．']
['1', '吨', '菜籽', '可', '榨油', '(2)/(3)', '吨', '，', '照', '这样', '计算', '，', '15', '吨', '菜籽', '可', '榨油', '多少', '吨', '．']
['电影院', '里', '有', '1300', '个', '座位', '，', '学校', '有', '28', '个', '班', '，', '平均', '每个', '班', '有', '45', '人', '，', '有', '多少', '个', '座位', '空', '着', '？']
['1', '本书', '，', '已经', '看', '了', '(3)/(5)', '，', '还', '剩', '30', '页', '，', '则', '这本', '数', '的', '页数', '为', '多少', '页', '．']
['修', '一条', '公路', '，', '已经', '修', '完', '840', '米', '，', '还', '剩下', '全长', '的', '(3)/(4)', '．', '公路', '全长', '多少', '米', '？']
['1', '堆', '煤', 

['李', '刚', '看', '1', '本书', '，', '第一天', '看', '了', '(1)/(4)', '，', '第', '2', '天', '看', '了', '60', '页', '，', '这时', '看', '了', '的', '与', '未', '看', '的', '页数', '比', '是', '2', '：', '3', '，', '这', '本书', '一共', '有', '多少', '页', '？']
['利民', '食品厂', '生产', '牛奶', '饼干', '3.6', '', '吨', '，', '比', '生产', '的', '果汁', '饼干', '多', '(1)/(5)', '，', '两种', '饼干', '一共', '生产', '了', '多少', '吨', '？']
['1', '共有', '436', '人', '参观', '恐龙', '馆', '，', '平均', '分成', '4', '批', '，', '每批', '多少', '人', '？']
['小', '明', '买', '了', '一套', '《', '安徒生', '童话集', '》', '，', '付', '了', '74.8', '', '元', '，', '比', '原价', '优惠', '了', '12%', '．', '这', '套书', '定价', '多少', '元', '？']
['6', '月', '26', '日', '是', '国际禁毒日', '，', '首都', '禁毒', '会员', '会', '首次', '举办', '了', '以', '“', '提倡', '健康', '人生', '，', '全民', '参与', '禁毒', '”', '为', '主题', '的', '万', '人', '长', '走', '活动', '．', '由于', '当', '天下', '起', '了', '大雨', '，', '只有', '12000', '名', '学生', '参加', '了', '长', '走', '活动', '，', '比', '原', '计划', '参加', '长', '走', '的', '学生', '少', '(1)/(5)', '．', '原', '计划', '参加', '长', '走', '的', '学生', 

...

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




['1', '批', '煤', '用', '去', '25%', '，', '还', '剩', '48', '吨', '，', '这', '批', '煤', '共有', '多少', '吨', '．']
['学校', '的', '果园', '里', '有', '梨树', '15', '棵', '，', '苹果树', '20', '棵', '．', '梨树', '的', '棵', '数', '比', '苹果树', '少', '几分', '之', '几', '？']
['某校', '有', '学生', '800', '人', '，', '其中', '男生', '480', '人', '，', '男生', '比', '女生', '多', '几', '人', '？']
['学校', '原有', '粉笔', '25', '盒', '，', '又', '买来', '43', '盒', '，', '正好', '是', '彩色', '粉笔', '的', '4', '倍', '，', '学校', '有', '彩色', '粉笔', '多少', '盒', '？']
['小', '玲', '家', '到', '学校', '的', '路程', '是', '800', '米', '．', '今天', '，', '她', '从', '家', '到', '学校', '，', '已', '行', '了', '全程', '的', '(7)/(10)', '，', '现在', '小', '玲', '离家', '多', '远', '？']
['(9)/(20)', '与', '一个', '数', '合', '起来', '是', '(11)/(20)', '，', '这个', '数', '=', '？']
['春风', '小学', '六年级', '有', '4', '个', '班', '，', '其中', '6', '（', '1', '）', '班', '有', '48', '人', '，', '正好', '相当于', '全', '级', '人数', '的', '(6)/(25)', '，', '春风', '小学', '六年级', '一共', '有', '多少', '人', '？']
['学校', '图书室', '有', '故事书', '562', '本', '，', '比', '文艺', '书', '多

['刘', '叔叔', '从', 'A', '地', '到', 'B', '地', '平均', '每', '小时', '行驶', '58.5', '', '千米', '，', '2', '小时', '到达', '，', '返回', '时', '用', '2.5', '', '小时', '，', '求', '返回', '时', '的', '速度', '？']
['亮', '亮', '买', '了', '6', '个', '练习本', '，', '燕', '燕', '买', '了', '3', '个', '练习本', '．', '每个', '练习本', '0.5', '', '元', '钱', '，', '亮', '亮', '比', '燕', '燕', '多', '花', '多少', '钱', '？']
['从', '18.3', '', '里', '减去', '4.5', '', '的', '4', '倍', '，', '所得', '的', '差', '被', '3', '除', '，', '结果', '=', '？']
['1', '个', '长方体', '，', '高', '减少', '一些', '后', '，', '体积', '就', '减少', '20', '立方厘米', '，', '剩下', '的', '是', '棱', '长', '5', '厘米', '的', '正方体', '，', '高', '减少', '了', '多少', '厘米', '．']
['5', '千克', '的', '(1)/(9)', '与', '1', '千克', '的', '多少', '相等', '．']
['1', '辆', '汽车', '行', '1', '千米', '耗油', '(1)/(12)', '升', '，', '照', '这样', '计算', '，', '行', '(3)/(4)', '千米', '耗油', '多少', '升', '．']
['1', '根', '绳子', '的', '长度', '等于', '它', '本身', '长度', '的', '(1)/(3)', '+', '10', '米', '，', '这', '绳子', '长', '多少', '米', '．']
['1', '个', '等腰三角', '形', '一边', '长', '4', '厘米', '

['1', '列', '火车', '经过', '一个', '路标', '需要', '5', '秒钟', '，', '通过', '300', '米', '的', '山洞', '要', '20', '秒钟', '，', '经过', '一座', '800', '米', '的', '大桥', '需要', '多少', '秒', '．']
['三年级', '学生', '扎', '了', '125', '朵', '红花', '和', '35', '朵', '黄花', '．', '他们', '将', '这些', '花', '送给', '幼儿园', '的', '5', '个', '幼儿班', '，', '平均', '每个', '班', '幼儿', '可以', '得到', '多少', '朵花', '？']
['125', '*', '80', '*', '4', '*', '2.5', '', '=', '．']
['3.2', '', '与', '1.7', '', '的', '差', '乘以', '4', '，', '所得', '的', '积', '去除', '2.4', '', '，', '商', '=', '？']
['挖', '一条', '水渠', '，', '如果', '每天', '挖', '全长', '的', '15%', '又', '20', '米', '，', '那么', '6', '天', '正好', '挖', '完', '．', '这', '一条', '水渠', '全长', '多少', '米', '？']
['1', '台', '彩电', '先', '降价', '20%', '，', '现在', '要', '涨价', '百分之几', '才能', '以', '原价', '出售', '？']
['1', '份', '搞', '件', '，', '已经', '打印', '好', '了', '24', '页', '，', '比', '剩下', '的', '页面', '少', '20%', '，', '这份', '稿件', '多少', '页', '？']
['沃尔玛', '超市', '之前', '塑料袋', '的', '日均', '使用量', '为', '20000', '个', '，', '实施', '限', '塑', '令', '以后', '日', '用量', '下降'

['果园', '里', '有', '果树', '1200', '棵', '，', '其中', '梨树', '占', '40%', '，', '桃树', '占', '20%', '，', '两种', '果树', '共有', '多少', '棵', '？']
['1', '辆', '汽车', '行', '7.5', '', '千米', '需要', '汽油', '(3)/(5)', '升', '，', '那么', '用', '1', '升', '汽油', '可行', '多少', '千米', '．']
['李老师', '买', '书', '用', '去', '76.8', '', '元', '，', '买', '5', '千克', '苹果', '共用', '去', '12', '元', '，', '她', '带', '了', '100', '元', '，', '还', '剩下', '多少', '元', '？']
['笑笑', '对', '淘气', '说', '：', '“', '我们', '班', '人数', '比', '你们', '班', '多', '20%', '．', '”', '淘气', '对', '笑笑', '说', '“', '我们', '班', '比', '你们', '班', '少', '8', '人', '．', '”', '笑笑', '班', '一共', '有', '多少', '人', '．']
['李', '明', '每月', '收入', '1900', '元', '，', '按规定', '应', '缴纳', '8%', '的', '个人所得税', '，', '李', '明', '实际', '月', '收入', '=', '多少', '元', '？']
['学校', '买来', '3', '箱', '图书', '，', '每箱', '120', '本', '，', '平均', '分给', '6', '个', '年级', '，', '平均', '每个', '年级', '分', '得', '多少', '本', '？']
['妈妈', '买', '了', '15', '个', '梨', '，', '小', '华', '吃掉', '3', '个', '后', '，', '把', '剩下', '平均', '放在', '3', '个', '袋子', '里', '，',

['镇海', '雅乐', '学校', '二年级', '的', '小朋友', '到', '一条', '小路', '的', '一边', '植树', '．', '小朋友', '们', '每隔', '2', '米', '种', '一棵树', '（', '马路', '两头', '都', '种', '了', '树', '）', '，', '最后', '发现', '一共', '种', '了', '11', '棵', '，', '这', '条', '小路', '长', '多少', '米', '．']
['1', '个', '工程队', '挖土', '，', '第一天', '挖', '了', '316', '方', '，', '从', '第', '2', '天', '开始', '每天', '都', '挖', '230', '方', '，', '连续', '挖', '了', '6', '天', '，', '这个', '工程队', '一周', '共', '挖土', '多少', '方', '？']
['小', '明', '看', '一本', '故事书', '，', '第一天', '看', '了', '全书', '的', '(1)/(6)', '，', '第', '2', '天', '看', '了', '24', '页', '，', '第', '3', '天', '看', '的', '页数', '是', '前两天', '看', '的', '总数', '的', '150%', '，', '这时', '还有', '全书', '的', '(1)/(4)', '没有', '看', '，', '那么', '这', '本书', '一共', '多少', '页', '．']
['从', '甲地', '到', '乙地', '，', '如果', '骑', '自行车', '每', '小时', '行驶', '16', '千米', '，', '4', '小时', '可以', '到达', '，', '如果', '乘', '汽车', '只', '需要', '2', '小时', '，', '汽车', '每', '小时', '行驶', '多少', '千米', '？']
['小', '刚', '的', '体重', '是', '28.4', '', '千克', '，', '小强', '的', '体重', '是', '小', '刚

['甲乙', '两个', '圆柱体', '容器', '，', '底', '面积', '之', '比', '是', '5', '：', '3', '，', '甲', '容器', '水深', '20', '厘米', '，', '乙', '容器', '水深', '10', '厘米', '，', '再', '往', '容器', '里', '注入', '同样', '多', '的', '水', '，', '使', '两个', '容器', '中', '的', '水深', '相等', '，', '这时', '水深', '多少', '厘米', '．']
['王', '叔叔', '从', '县城', '出发', '去', '王', '庄', '送', '化肥', '．', '去', '时', '按照', '每', '小时', '40', '千米', '的', '速度', '用', '了', '3', '小时', '，', '返回', '时', '用', '了', '2', '小时', '；', '返回', '时', '平均', '每', '小时', '行', '多少', '千米', '？']
['某', '空调', '生产', '车间', '，', '原', '计划', '每天', '生产', '40', '台', '空调', '，', '15', '天', '可以', '完成', '任务', '；', '实际', '每天', '比', '原', '计划', '多', '生产', '10', '台', '，', '实际', '生产', '这', '批', '空调', '用', '了', '多少', '天', '？']
['从', '一个', '数里', '减去', '(11)/(18)', '后', '是', '(5)/(18)', '，', '这个', '数', '是', '几', '？']
['春晖', '小学', '的', '老师', '们', '带领', '学生', '外出', '春游', '，', '参加', '春游', '的', '老师', '占', '15%', '，', '其余', '的', '是', '学生', '．', '在', '学生', '中', '男', '、', '女生', '人数', '的', '比', '是', '9', '：', '8', '，', '

['大厅', '里', '有', '4', '根', '圆柱', '，', '每', '根', '底面', '直径', '为', '1', '米', '，', '高', '为', '8', '米', '．', '在', '这些', '圆柱', '的', '表面', '涂', '油漆', '，', '平均', '每平方米', '用', '油漆', '0.8', '', '千克', '，', '共', '需', '油漆', '多少', '千克', '？']
['我国', '是', '世界', '上', '13', '个', '贫', '水', '国家', '之1', '，', '水资源', '人均', '占有量', '只有', '2300', '立方米', '，', '约', '为', '世界', '人均', '水平', '的', '(1)/(4)', '，', '世界', '水资源', '人均', '占有量', '=', '？']
['学校', '买', '了', '24', '个', '排球', '，', '买', '的', '足球', '是', '排球', '的', '(5)/(4)', '，', '买', '的', '足球', '和', '排球', '一共', '多少', '个', '？']
['多少', '吨', '的', '4', '倍', '是', '120', '吨', '．']
['1', '个', '平行四边形', '的', '面积', '是', '33.6', '', '平方厘米', '，', '其', '底边', '长', '是', '8.4', '', '厘米', '，', '那么', '它', '的', '高', '=', '多少', '厘米', '．']
['上海', '广播', '电视塔', '高', '468', '米', '，', '中央', '广播', '电视塔', '高', '405', '米', '，', '上海', '广播', '电视塔', '比', '中央', '广播', '电视塔', '高', '多少', '米', '？']
['某', '厂', '去年', '上半年', '生产', '洗衣机', '36', '万台', '，', '是', '下半年', '产量', '的', '(4)/(5)', '．', '这个', '

['1', '吨', '菜籽', '可', '榨油', '(2)/(3)', '吨', '，', '照', '这样', '计算', '，', '15', '吨', '菜籽', '可', '榨油', '多少', '吨', '．']
['电影院', '里', '有', '1300', '个', '座位', '，', '学校', '有', '28', '个', '班', '，', '平均', '每个', '班', '有', '45', '人', '，', '有', '多少', '个', '座位', '空', '着', '？']
['1', '本书', '，', '已经', '看', '了', '(3)/(5)', '，', '还', '剩', '30', '页', '，', '则', '这本', '数', '的', '页数', '为', '多少', '页', '．']
['修', '一条', '公路', '，', '已经', '修', '完', '840', '米', '，', '还', '剩下', '全长', '的', '(3)/(4)', '．', '公路', '全长', '多少', '米', '？']
['1', '堆', '煤', '第一次', '运走', '它', '的', '(1)/(6)', '，', '第', '2', '次', '运走', '21', '吨', '，', '还', '剩下', '14', '吨', '，', '这', '堆', '煤', '原有', '多少', '吨', '？']
['学校', '美术', '小组', '有', '24', '人', '，', '是', '航模', '小组', '人数', '的', '(4)/(5)', '，', '科技', '小组', '是', '航模', '小组', '的', '(3)/(5)', '．', '科技', '小组', '有', '多少', '人', '？']
['1', '条', '马路', '的', '一边', '从头到尾', '共', '种', '了', '10', '棵', '树', '，', '每', '两棵树', '之间', '相隔', '8', '米', '，', '这', '条', '马路', '长', '多少', '米', '？']
['小', '华', '从', '甲地'

['1', '个数', '加上', '8', '，', '然后', '乘', '6', '，', '再', '减去', '20', '等于', '58', '，', '这个', '数', '=', '？']
['56', '名', '少先队员', '参加', '学校', '劳动', '，', '其中', '(3)/(7)', '的', '人', '打扫', '礼堂', '，', '剩下', '的', '队员', '中', '(3)/(8)', '的', '人', '打扫', '操场', '，', '再', '剩下', '的', '(1)/(4)', '打扫', '教室', '，', '其余', '的', '人', '负责', '打扫', '室外', '空地', '，', '问', '打扫', '空地', '的', '有', '多少', '人', '？']
['1', '座', '山上', '共有', '白杨树', '275', '棵', '，', '梧桐树', '是', '白杨树', '的', '10', '倍', '还', '多', '5', '棵', '，', '白杨树', '和', '梧桐', '共', '多少', '棵', '？']
['甲乙', '两种', '儿童', '服饰', '原价', '相同', '，', '甲种', '儿童', '服饰', '按', '0.5', '', '销售', '，', '乙种', '儿童', '服饰', '按', '0.6', '', '销售', '，', '王', '阿姨', '共', '花', '121', '元', '购买', '这', '两种', '儿童', '服饰', '各', '一件', '，', '这', '两种', '儿童', '服饰', '每件', '原价', '多少', '元', '？']
['爸爸', '从', '菜场', '买', '回', '2.4', '', '千克', '肉', '，', '每千克', '26.5', '', '元', '，', '还', '买', '回', '1.5', '', '千克', '鸡蛋', '，', '每千克', '64', '元', '，', '爸爸', '1', '共用', '了', '多少', '钱', '？']
['陈', '师傅', '用', '铁皮',

...


['某', '厂', '计划', '6', '月份', '生产', '彩电', '585', '台', '，', '实际', '每天', '产量比', '原', '计划', '增加', '(2)/(13)', '，', '照', '这样', '计算', '，', '可以', '提早', '少', '天', '完成', '生产', '计划', '？', '（', '按', '30', '天', '计算', '）']
['人', '的', '血液', '大约', '占', '体重', '的', '(1)/(13)', '，', '血液', '里', '大约', '有', '(2)/(3)', '是', '水', '．', '王', '壮', '的', '体重', '是', '39', '千克', '，', '他', '的', '血液', '里', '大约', '含水', '多少', '千克', '？']
['甲', '、', '乙', '两地', '相距', '720', '千米', '，', '一辆', '汽车', '从', '甲地', '开往', '乙地', '需要', '9', '小时', '，', '如果', '要求', '汽车', '提前', '1', '小时', '到达', '乙地', '．', '汽车', '平均速度', '应', '提高', '多少', '千米', '/', '时', '？']
['已知', '两个', '数', '的', '和', '是', '85.7', '', '，', '其中', '一个', '加数', '是', '15.7', '', '，', '求', '另', '一个', '加数', '=', '？']
['修', '一条', '公路', '，', '计划', '每天', '修', '200', '米', '15', '天', '可以', '修', '完', '；', '实际', '只', '修', '了', '12', '天', '就', '完工', '了', '，', '实际', '每天', '修', '了', '多少', '米', '？']
['把', '一根', '木材', '锯', '成', '4', '段', '要', '用', '12', '分钟', '，', '照', '这样', '计算', '，', '锯

['小', '丽', '的', '身高', '比', '小', '华', '矮', '(1)/(16)', '，', '小', '丽', '的', '身高', '1.35', '米', '，', '小', '华', '身高', '多少', '米', '？']
['比', '的', '后', '项', '是', '(4)/(15)', '，', '比值', '是', '(4)/(3)', '，', '比', '的', '前项', '=', '．']
['小', '婷', '跳绳', '原来', '每分钟', '跳', '75', '下', '，', '现在', '每分钟', '可以', '跳', '100', '下', '．', '原来', '4', '分钟', '跳', '的', '下', '数', '，', '现在', '只要', '跳', '几分钟', '？']
['甲', '．', '乙', '两', '人', '分别', '从', '两地', '同时', '出发', '相对', '而', '行', '，', '甲', '每分钟', '行', '70', '米', '，', '乙', '每分钟', '行', '50', '米', '，', '20', '分钟', '后', '，', '两', '人', '过', '了', '相遇', '点', '又', '相距', '100', '米', '．', '问', '两地', '间', '的', '路程', '=', '多少', '米', '？']
['蔬菜', '实验', '基地', '今年', '共', '收获', '8', '吨', '蔬菜', '，', '其中', '黄瓜', '的', '重量', '占', '(2)/(5)', '，', '黄瓜', '的', '重量', '是', '茄子', '的', '(4)/(5)', '，', '今年', '收', '茄子', '多少', '吨', '？']
['修路', '队', '修', '一条', '长', '800', '米', '的', '路', '，', '第一天', '修', '了', '全长', '的', '(1)/(4)', '，', '第', '2', '天', '修', '了', '第一天', '的', '(4)/(5)', '，', '两天',

['1', '支', '钢笔', '的', '售价', '是', '75', '元', '，', '打', '0.8', '', '后', '的', '售价', '=', '多少', '元', '．']
['修', '一条', '公路', '，', '第一天', '修', '了', '全长', '的', '25%', '，', '第', '2', '天', '修', '了', '全长', '的', '30%', '，', '还', '剩下', '360', '米', '没有', '修', '，', '这', '条', '路', '全长', '=', '多少', '米', '？']
['小强', '赢', '了', '11', '颗', '玻璃球', '后', '，', '正好', '比', '他', '原来', '的', '玻璃球', '多', '(1)/(10)', '，', '小强', '现在', '有', '多少', '颗', '玻璃球', '？']
['图书室', '新', '买来', '200', '本', '科技', '书', '，', '新', '买来', '的', '故事书', '是', '科技', '书', '的', '5', '倍', '，', '两种', '书', '共有', '多少', '本', '？']
['有', '一堆', '3', '立方米', '的', '沙土', '，', '要', '铺', '在', '长', '6', '米', '，', '宽', '2', '米', '的', '跑道', '上', '，', '可以', '铺', '多', '厚', '？']
['兔脚', '有', '100', '只', '，', '鸡脚', '的', '只', '数', '是', '兔脚', '只', '数', '的', '60%', '，', '鸡兔', '脚数', '共', '多少', '只', '．']
['王老师', '要', '批改', '48', '篇', '作文', '，', '批改', '了', '4', '小时', '后', '，', '还', '剩', '12', '篇', '，', '平均', '每', '小时', '批改', '几篇', '？']
['1', '种', '大豆', '每千克', '含油', '(4)/

['爷爷', '今年', '72', '岁', '，', '爸爸', '年龄', '是', '爷爷', '的', '(5)/(9)', '，', '我', '的', '年龄', '是', '爸爸', '的', '(3)/(10)', '．', '我', '今年', '多少岁', '？']
['公园', '里', '有', '个', '圆形', '花坛', '，', '周长', '180', '米', '．', '在', '花坛', '的', '4', '周', '，', '每隔', '4', '米', '种', '1', '棵', '冬青树', '，', '一共', '可以', '种', '多少', '棵', '．']
['红', '黑', '球', '共', '40', '个', '，', '其中', '红球', '占', '62.5%', '，', '红球', '比', '黑', '球', '多', '多少', '个', '？']
['1', '桶', '油', '重', '90', '千克', '，', '第一次', '倒', '出', '(2)/(5)', '，', '第', '2', '次', '倒', '出', '(4)/(5)', '千克', '，', '还', '剩', '多少', '千克', '？']
['甲乙', '两车', '同时', '从', 'A', '、', 'B', '两地', '相向', '而', '行', '，', '甲', '车', '每', '小时', '行', '55', '千米', '，', '乙', '车', '每', '小时', '行', '65', '千米', '，', '3', '小时', '后', '两车', '还', '差', '15', '千米', '才能', '相遇', '，', 'A', '、', 'B', '两地', '相距', '多少', '千米', '？']
['“', '6', '1', '”', '儿童节', '，', '学校', '举行', '绘画', '比赛', '．', '五年级', '获奖作品', '总数', '为', '48', '张', '，', '是', '四年级', '获奖', '总数', '的', '(4)/(3)', '，', '四年级', '获奖', '总数', '相当于',

['三年级', '学生', '6', '个', '组', '做', '儿童玩具', '72', '件', '，', '平均', '分给', '4', '个', '幼儿班', '，', '每个', '班', '分', '玩具', '多少', '个', '？']
['1', '件', '衬衫', '100', '元', '，', '一件', '毛衣', '的', '价格比', '它', '的', '2', '倍', '还', '多', '6', '元', '，', '毛衣', '的', '价格', '=', '多少', '元', '．']
['16', '/', '2', '的', '商', '加上', '4', '个', '3.5', '', '的', '和', '，', '结果', '=', '？']
['1', '个', '工程队', '要', '修', '一条', '长', '22400', '米', '的', '公路', '，', '计划', '每天', '修', '320', '米', '，', '实际', '每天', '修', '400', '米', '，', '实际', '比', '计划', '提前', '几天', '修', '完', '？']
['1', '辆', '汽车', '从', '甲地', '开往', '乙地', '，', '第一天', '走', '350', '千米', '，', '第', '2', '天', '走', '的', '比', '第一天', '多', '20%', '，', '没', '走', '的', '比', '两天', '共', '走', '的', '多', '(1)/(14)', '，', '甲', '、', '乙', '两地', '相距', '多少', '千米', '？']
['1', '桶', '油', '，', '如果', '倒', '出', '32', '千克', '，', '还', '剩', '(3)/(5)', '．', '这', '桶', '油', '原来', '重', '多少', '千克', '？']
['张', '叔叔', '这个', '月', '的', '工资总额', '为', '1900', '元', '．', '按照', '个人所得税法', '的', '规定', '，', '超过', '1600',

In [52]:
# data_dict

In [53]:
# data_dict[19589]

In [54]:
# dff = pd.DataFrame.from_dict(data_dict)
# dff.T.head()

In [55]:
def process_ans( ans):
#         print("orig ans ",ans)
        try:
            float(ans)
            return ans
        except:
            if '%' in ans:
                ans = ans[:-1]
                ans = float(ans)/100
                return str(ans)
            else:
                s_1 = ans.find('(')
                if s_1 >0:
                    num_pre = ans[:s_1]
                else:
                    num_pre = 0 
#                 print(ans)
                s_1 = ans.find('(')
                e_1 = ans.find(')', s_1+1)
                num_1 = ans[s_1+1:e_1]
                s_2 = ans.find('(', e_1)
                e_2 = ans.find(')', s_2)
                num_2 = ans[s_2+1:e_2]
#                 print("process ans ",num_pre, num_1,num_2)
                ans = float(num_pre)+float(num_1)/float(num_2)
                return str(ans)

def process_single_num( ans, eqn_list, index):
    alphas = ['a', 'b', 'c', 'd', 'e', 'f', 'g', 'h', 'i', 'j', 'k', 'l', 'm', 'n', 'o', 'p', 'q', 'r', 's', 't', 'u', 'v', 'w', 'x', 'y', 'z']
    try:
        float(ans)
        return ans, eqn_list
    except:
        if '%' in ans:
            
            ans = ans[:-1]
#             this can be removed
            for itr_a in range(len(eqn_list)):
                if eqn_list[itr_a] == ans:
                    eqn_list[itr_a] = 'temp_' + alphas[index]
            
            ans = float(ans)/100
            for itr_a in range(len(eqn_list)):
                if eqn_list[itr_a] == str(ans):
                    eqn_list[itr_a] = 'temp_' + alphas[index]
            return str(ans), eqn_list
        else:
#             print(ans)
            s_1 = ans.find('(')
            if s_1 >0:
                num_pre = ans[:s_1]
            else:
                num_pre = 0 
#             print(num_pre)
#             print(ans)
            s_1 = ans.find('(')
#             s_1 = ans.find('(', s_1+1)
            e_1 = ans.find(')', s_1+1)
#             print(s_1,e_1)
            num_1 = ans[s_1+1:e_1]
            s_2 = ans.find('(', e_1)
            e_2 = ans.find(')', s_2)
            num_2 = ans[s_2+1:e_2]
#             print(num_pre, num_1,num_2)
            ans = (float(num_pre)*float(num_2)+float(num_1))/float(num_2)
            return str(ans), eqn_list
#             print("answer here is ",ans)
#             s_1 = ans.find('(')
#             if s_1 >0:
#                 num_pre = ans[:s_1]
#             else:
#                 num_pre = 0 
            
#             e_1 = ans.find('/', s_1+1)
#             num_1 = ans[s_1+1:e_1]
#             e_2 = ans.find(')', e_1)
#             num_2 = ans[e_1+1:e_2]
#             print(num_pre, num_1,num_2)
#             ans = float(num_pre)+float(num_1)/float(num_2)
#             print("answer processed is ",ans)
#             return str(ans)

def process_num_list( num_list, eqn_list):
    new_num_list = []
    i = 0
    for num in num_list:
        num, eqn_list =process_single_num(num, eqn_list, i)
        new_num_list.append(num)
        i += 1
    return new_num_list, eqn_list

def check_ans( num_list, template, ans):
    alphabets = 'abcdefghijklmnopqrstuvwxyz'
    new_equ = []
    for elem in template:
        if 'temp' in elem:
            new_equ.append(str(num_list[alphabets.find(elem[-1])]))
        else:
            new_equ.append(elem)
    return equ_api_1(new_equ, ans)

In [56]:
#  Convert infix expression to suffix expression
def postfix_equation(equ_list):
    equ_list = equ_list[2:]
    stack = []
    post_equ = []
    op_list = ['+', '-', '*', '/', '^']
    priori = {'^': 3, '*': 2, '/': 2, '+': 1, '-': 1}
    for elem in equ_list:
        if elem == '(':
            stack.append('(')
        elif elem == ')':
            while 1:
                op = stack.pop()
                if op == '(':
                    break
                else:
                    post_equ.append(op)
        elif elem in op_list:
            while 1:
                if not stack:
                    break
                elif stack[-1] == '(':
                    break
                elif priori[elem] > priori[stack[-1]]:
                    break
                else:
                    op = stack.pop()
                    post_equ.append(op)
            stack.append(elem)
        else:
            post_equ.append(elem)
    while stack:
        post_equ.append(stack.pop())
    return post_equ

In [57]:
# data_dict = data_dict_
i=0
for key in data_dict:
    elem = data_dict[key]
    elem_tuple = elem['tuple']
    data_dict[key] = {'text':'','target_template':[],'gen_template':[],'num_list':[],'ans':0}
    data_dict[key]['text'] = ' '.join(elem_tuple[0]) # str
    data_dict[key]['numtemp_order'] = elem_tuple[4]
    data_dict[key]['num_position'] = elem_tuple[5]
    (data_dict[key]['num_list'], data_dict[key]['target_template']) = process_num_list(elem_tuple[2], elem_tuple[1]) # [float, float]
#     data_dict[key]['target_template'] = elem_tuple[1] # list x= temp_a ,,,
    data_dict[key]['post_template'] = postfix_equation(data_dict[key]['target_template'])
    data_dict[key]['ans'] = process_ans(elem['solution']) # float 
    i+=1
#     if(i==10):
#         break

In [58]:
len(data_dict)

23160

In [59]:
data_dict[14946]

{'text': '北京 和 上海 相距 temp_a km ． 甲乙 两列 直快 火车 同时 从 北京 和 上海 相对 开出 ， temp_b 小时 后 两车 相遇 ， 甲 车 每 小时 行 temp_c 千米 ， 乙 车 每 小时 行 多少 千米 ？',
 'target_template': ['x', '=', 'temp_a', '/', 'temp_b', '-', 'temp_c'],
 'gen_template': [],
 'num_list': ['1320', '6', '120'],
 'ans': '100',
 'numtemp_order': ['temp_a', 'temp_b', 'temp_c'],
 'num_position': [4, 19, 30],
 'post_template': ['temp_a', 'temp_b', '/', 'temp_c', '-']}

In [60]:
data_dict_new = {}
ids=[]
for el in data_dict:
    temp_list = data_dict[el]["target_template"]
    flag=0
    for sym in temp_list:
        if(sym[0].isdigit() and sym!='1'):
#             print(el,temp_list)
            ids.append(el)
            flag=1
            break
    if(flag):
        continue
    else:
        data_dict_new[el] = data_dict[el]

In [61]:
len(data_dict_new)

23129

In [62]:
# datajson = dff.to_json(orient='index')
with open("math23k_0108.json", 'w') as f:
    json.dump(data_dict_new, f)

In [45]:
dff = pd.DataFrame.from_dict(data_dict_new)
dff = dff.T
dff.head()
# dff.shape

text  \
1  镇海 雅乐 学校 二年级 的 小朋友 到 一条 小路 的 一边 植树 ． 小朋友 们 每隔 ...   
2  temp_a 个 工程队 挖土 ， 第一天 挖 了 temp_b 方 ， 从 第 temp_...   
3  小 明 看 一本 故事书 ， 第一天 看 了 全书 的 temp_a ， 第 temp_b ...   
4  从 甲地 到 乙地 ， 如果 骑 自行车 每 小时 行驶 temp_a 千米 ， temp_...   
5  小 刚 的 体重 是 temp_a 千克 ， 小强 的 体重 是 小 刚 的 temp_b ...   

                                     target_template gen_template  \
1              [x, =, (, temp_b, -, 1, ), *, temp_a]           []   
2  [x, =, temp_b, +, temp_d, *, (, temp_e, -, tem...           []   
3  [x, =, (, temp_c, +, temp_c, *, temp_e, ), /, ...           []   
4               [x, =, temp_a, *, temp_b, /, temp_c]           []   
5                          [x, =, temp_a, *, temp_b]           []   

                                     num_list    ans  \
1                                     [2, 11]     20   
2                         [1, 316, 2, 230, 6]   1466   
3  [0.16666666666666666, 2, 24, 3, 1.5, 0.25]    180   
4                                  [16, 4, 2]     32   
5                                 [28.4, 1.4]  39.76   

                                      numtemp_order              num_position  \
1                                  [temp_a, temp_b]                  [16, 34]   
2          [temp_a, temp_b, temp_c, temp_d, temp_e]        [0, 8, 13, 19, 25]   
3  [temp_a, temp_b, temp_c, temp_d, temp_e, temp_f]  [11, 14, 18, 22, 33, 39]   
4                          [temp_a, temp_b, temp_c]              [11, 14, 24]   
5                                  [temp_a, temp_b]                   [5, 16]   

                                       post_template  
1                          [temp_b, 1, -, temp_a, *]  
2          [temp_b, temp_d, temp_e, temp_a, -, *, +]  
3  [temp_c, temp_c, temp_e, *, +, 1, temp_a, -, t...  
4                     [temp_a, temp_b, *, temp_c, /]  
5                                [temp_a, temp_b, *]

# Baseline Code

In [8]:
with open("math23k_dolphin.json",'r') as f:
    dff = json.load(f)
dff = pd.read_json(dff)
dff = dff.T

In [19]:
def postfix_equation(equ_list):
    stack = []
    post_equ = []
    op_list = ['+', '-', '*', '/', '^']
    priori = {'^': 3, '*': 2, '/': 2, '+': 1, '-': 1}
    for elem in equ_list:
        if elem == '(':
            stack.append('(')
        elif elem == ')':
            while 1:
                op = stack.pop()
                if op == '(':
                    break
                else:
                    post_equ.append(op)
        elif elem in op_list:
            while 1:
                if not stack:
                    break
                elif stack[-1] == '(':
                    break
                elif priori[elem] > priori[stack[-1]]:
                    break
                else:
                    op = stack.pop()
                    post_equ.append(op)
            stack.append(elem)
        else:
            post_equ.append(elem)
    while stack:
        post_equ.append(stack.pop())
    return post_equ

def post_solver(post_equ):
    try:
        stack = [] 
        op_list = ['+', '-', '/', '*', '^']
        for elem in post_equ:
            if elem not in op_list:
                op_v = elem
                if '%' in op_v:
                    op_v = float(op_v[:-1])/100.0
                stack.append(str(op_v))
            elif elem in op_list:
                op_v_1 = stack.pop()
                op_v_1 = float(op_v_1)
                op_v_2 = stack.pop()
                op_v_2 = float(op_v_2)
                if elem == '+':
                    stack.append(str(op_v_2+op_v_1))
                elif elem == '-':
                    stack.append(str(op_v_2-op_v_1))
                elif elem == '*':
                    stack.append(str(op_v_2*op_v_1))
                elif elem == '/':
                    if op_v_1 == 0:
                        return nan
                    stack.append(str(op_v_2/op_v_1))
                else:
                    stack.append(str(op_v_2**op_v_1))
        return stack.pop()
    except:
#         print(post_equ)
        return None

def getBaseline(lst):
#     lst = list(np.random.permutation(lst))
    ops = ['-','+','*','/']
    ops_nodiv = ['-','+','*']
    ops=ops_nodiv
#     ops_nodiv = ['-','+','*']
    eq_list = [str(lst[0])]
    for i in range(1,len(lst)):
        if(lst[i][0]=='0'):
            op = random.choice(ops_nodiv)
        else:
            op = random.choice(ops)
        eq_list.append(op)
        eq_list.append(str(lst[i]))
    peq = postfix_equation(eq_list)
    return post_solver(peq) 

In [16]:
best = 0.0
for i in range(10):
    dff["baseline"] = dff["num_list"].apply(lambda x : getBaseline(x))
    a_ = dff["ans"]
    b_ = dff["baseline"]
    a,b = [],[]
    for i in range(len(a_)):
        if ';' in a_[i] or 'e' in a_[i]:
            continue
        if b_[i] is None:
            continue
        a.append(a_[i])
        b.append(b_[i])
    a = [int(float(x)) for x in a]
    b = [int(float(x)) for x in b]
    acc = sum(1 for x,y in zip(a,b) if x == y) / len(a)
    if(acc>best):
        best=acc
best
    

0.0620762252701322

In [20]:
best = 0.0
for i in range(10):
    dff["baseline"] = dff["num_list"].apply(lambda x : getBaseline(x))
    a_ = dff["ans"]
    b_ = dff["baseline"]
    a,b = [],[]
    for i in range(len(a_)):
        if ';' in a_[i] or 'e' in a_[i]:
            continue
        if b_[i] is None:
            continue
        a.append(a_[i])
        b.append(b_[i])
    a = [int(float(x)) for x in a]
    b = [int(float(x)) for x in b]
    acc = sum(1 for x,y in zip(a,b) if x == y) / len(a)
    if(acc>best):
        best=acc
best

0.06501749280163473